In [ ]:
#standard imports
import pandas as pd
import numpy as np
from google.colab import drive
from geopy.geocoders import Nominatim
import folium
import io
import matplotlib.pyplot as plt
from PIL import Image

In [ ]:
#mounting from google drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
#reading csv
raw_facility = pd.read_csv('/content/drive/Shareddrives/Rice Datathon 2023/Copy of beginner.csv')
raw_facility.head(10)

Facility Name  \
0               Ohana Memorials Mammography Services   
1                         31 Medical Group Aviano AB   
2                 35th Medical Group Misawa AB Japan   
3    374th MDG Unit 5225 SGCR Yokota AB APO AP 96328   
4                                375th Medical Group   
5                3D Mammography of Southwest Montana   
6                         3T Imaging of Morton Grove   
7                    48th Medical Group 48 MSGS/SGCR   
8                            56th Medical Group/SGSS   
9  88th Med. Group DTS/ SGQQ Wright Patterson Med...   

                   Address 1                Address 2            Address 3  \
0         1515 W Yakima Ave.                      NaN                  NaN   
1                      Italy         31 Medical Group            Unit 6180   
2                  Unit 5024                      NaN                  NaN   
3             Unit 5225 SGCR      374th Medical Group                  NaN   
4            310 W Losey St.                      NaN                  NaN   
5                       Inc.          800 W. Platinum               Unit D   
6  9000 Waukengan Rd Ste 110                      NaN                  NaN   
7                  Unit 5115             48 MSGS/SGCR                  NaN   
8                   Luke AFB  7219 N. Litchfield Road  Luke Air Force Base   
9        4881 Sugar Maple Dr                      NaN                  NaN   

                   City            State    Zip Code        Phone  \
0                Yakima               WA       98902  509574-3863   
1                   NaN  Air Post Office          AE         9604   
2                   APO               AP  96319-5300  8.13118E+11   
3                   APO               AP       96328    425522510   
4             Scott AFB               IL  62225-5252  618256-1494   
5                   NaN            Butte          MT        59701   
6          Morton Grove               IL       60053  847213-2700   
7                   APO               AE  09461-5115  4.41639E+11   
8                   NaN         Luke AFB          AZ   85309-1525   
9  Wright Patterson AFB               OH       45433  937257-2168   

           Fax   Unnamed: 9 Unnamed: 10 Unnamed: 11 Unnamed: 12  
0  509249-5319          NaN         NaN         NaN         NaN  
1  3.90434E+11      3904343         NaN         NaN         NaN  
2      8117677          NaN         NaN         NaN         NaN  
3    425302026          NaN         NaN         NaN         NaN  
4  618256-7253          NaN         NaN         NaN         NaN  
5  406299-3302  406299-3304         NaN         NaN         NaN  
6  847213-2709          NaN         NaN         NaN         NaN  
7      4416385          NaN         NaN         NaN         NaN  
8  623856-7618  623856-4009         NaN         NaN         NaN  
9  937257-5229          NaN         NaN         NaN         NaN

In [ ]:
#exploratory data analysis
raw_facility.shape

(8811, 13)

In [ ]:

#shift calls to the left
for i in range(raw_facility.shape[0]) :
  #case number 1: if LLC or Inc shifted everything to the right so city is filled incorrectly, shift based on the other columns
  if pd.isnull(raw_facility.iloc[i,4]) == False and ('Inc.' in raw_facility.iloc[i, 1] or 'LLC' in raw_facility.iloc[i, 1]):
    if pd.isnull(raw_facility.iloc[i,5]) and pd.isnull(raw_facility.iloc[i,6]) and pd.isnull(raw_facility.iloc[i,7]):
      raw_facility.iloc[i,4] = raw_facility.iloc[i,8]
      raw_facility.iloc[i,5] = raw_facility.iloc[i,9]
      raw_facility.iloc[i,6] = raw_facility.iloc[i,10]
      raw_facility.iloc[i,7] = raw_facility.iloc[i,11]
    elif pd.isnull(raw_facility.iloc[i,5]) and pd.isnull(raw_facility.iloc[i,6]):
      raw_facility.iloc[i,4] = raw_facility.iloc[i,7]
      raw_facility.iloc[i,5] = raw_facility.iloc[i,8]
      raw_facility.iloc[i,6] = raw_facility.iloc[i,9]
      raw_facility.iloc[i,7] = raw_facility.iloc[i,10]
    elif pd.isnull(raw_facility.iloc[i,5]):
      raw_facility.iloc[i,4] = raw_facility.iloc[i,6]
      raw_facility.iloc[i,5] = raw_facility.iloc[i,7]
      raw_facility.iloc[i,6] = raw_facility.iloc[i,8]
      raw_facility.iloc[i,7] = raw_facility.iloc[i,9]
    else:
      # print(raw_facility.iloc[i,4])
      raw_facility.iloc[i,4] = raw_facility.iloc[i,5]
      raw_facility.iloc[i,5] = raw_facility.iloc[i,6]
      raw_facility.iloc[i,6] = raw_facility.iloc[i,7]
      raw_facility.iloc[i,7] = raw_facility.iloc[i,8]
      
  #print("Row:", raw_facility.iloc[i,4])

  #case number 2: if the null values started at city
  if pd.isnull(raw_facility.iloc[i,4]) and pd.isnull(raw_facility.iloc[i,5]) and pd.isnull(raw_facility.iloc[i,6]) and pd.isnull(raw_facility.iloc[i,7]):
    raw_facility.iloc[i,4] = raw_facility.iloc[i,8]
    raw_facility.iloc[i,5] = raw_facility.iloc[i,9]
    raw_facility.iloc[i,6] = raw_facility.iloc[i,10]
    raw_facility.iloc[i,7] = raw_facility.iloc[i,11]
  elif pd.isnull(raw_facility.iloc[i,4]) and pd.isnull(raw_facility.iloc[i,5]) and pd.isnull(raw_facility.iloc[i,6]):
    raw_facility.iloc[i,4] = raw_facility.iloc[i,7]
    raw_facility.iloc[i,5] = raw_facility.iloc[i,8]
    raw_facility.iloc[i,6] = raw_facility.iloc[i,9]
    raw_facility.iloc[i,7] = raw_facility.iloc[i,10]
  elif pd.isnull(raw_facility.iloc[i,4]) and pd.isnull(raw_facility.iloc[i,5]):
    raw_facility.iloc[i,4] = raw_facility.iloc[i,6]
    raw_facility.iloc[i,5] = raw_facility.iloc[i,7]
    raw_facility.iloc[i,6] = raw_facility.iloc[i,8]
    raw_facility.iloc[i,7] = raw_facility.iloc[i,9]
  elif pd.isnull(raw_facility.iloc[i,4]):
    raw_facility.iloc[i,4] = raw_facility.iloc[i,5]
    raw_facility.iloc[i,5] = raw_facility.iloc[i,6]
    raw_facility.iloc[i,6] = raw_facility.iloc[i,7]
    raw_facility.iloc[i,7] = raw_facility.iloc[i,8]
    

In [ ]:
#more cleaning

states = ['AL', 'AK', 'AZ', 'AR', 'AR', 'CA', 'CO', 'CT', 'DE', 'FL', 'GA','HI', 'ID', 'IL', 'IN','IA', 'KS', 'KY', 'LA', 'ME', 'MD', 'MA', 'MI',
          'MN', 'MS', 'MO', 'MT', 'NE', 'NV', 'NH', 'NJ', 'NM', 'NY', 'NC', 'ND', 'OH', 
          'OK', 'OR', 'PA', 'RI','SC', 'SD', 'TN', 'TX', 'UT', 'VT', 'VA', 'WA','WV', 'WI', 'WY', 'PR']

for i in range(raw_facility.shape[0]) :
  if isinstance(raw_facility.iloc[i,6], str) and len(raw_facility.iloc[i,6]) == 2 and raw_facility.iloc[i,6] in states:
    raw_facility.iloc[i,4] = raw_facility.iloc[i,5]
    raw_facility.iloc[i,5] = raw_facility.iloc[i,6]
    raw_facility.iloc[i,6] = raw_facility.iloc[i,7]
    raw_facility.iloc[i,7] = raw_facility.iloc[i,8]
  elif isinstance(raw_facility.iloc[i,7], str) and len(raw_facility.iloc[i,7]) == 2 and raw_facility.iloc[i,7] in states:
    raw_facility.iloc[i,4] = raw_facility.iloc[i,6]
    raw_facility.iloc[i,5] = raw_facility.iloc[i,7]
    raw_facility.iloc[i,6] = raw_facility.iloc[i,8]
    raw_facility.iloc[i,7] = raw_facility.iloc[i,9]
  elif isinstance(raw_facility.iloc[i,8], str) and len(raw_facility.iloc[i,8]) == 2 and raw_facility.iloc[i,8] in states:
    raw_facility.iloc[i,4] = raw_facility.iloc[i,7]
    raw_facility.iloc[i,5] = raw_facility.iloc[i,8]
    raw_facility.iloc[i,6] = raw_facility.iloc[i,9]
    raw_facility.iloc[i,7] = raw_facility.iloc[i,10]
  elif isinstance(raw_facility.iloc[i,9], str) and len(raw_facility.iloc[i,9]) == 2 and raw_facility.iloc[i,9] in states:
    raw_facility.iloc[i,4] = raw_facility.iloc[i,8]
    raw_facility.iloc[i,5] = raw_facility.iloc[i,9]
    raw_facility.iloc[i,6] = raw_facility.iloc[i,10]
    raw_facility.iloc[i,7] = raw_facility.iloc[i,11]

In [ ]:
#Break up zip code
zip_code = raw_facility['Zip Code'].str.split(pat='-',n=1,expand=True)
raw_facility['Zip Code'] = zip_code[0]
raw_facility

Facility Name              Address 1  \
0                Ohana Memorials Mammography Services     1515 W Yakima Ave.   
1                          31 Medical Group Aviano AB                  Italy   
2                  35th Medical Group Misawa AB Japan              Unit 5024   
3     374th MDG Unit 5225 SGCR Yokota AB APO AP 96328         Unit 5225 SGCR   
4                                 375th Medical Group        310 W Losey St.   
...                                               ...                    ...   
8806                         Zwanger-Pesiri Radiology     160 Brentwood Road   
8807                         Zwanger-Pesiri Radiology  803-F Montauk Highway   
8808                         Zwanger-Pesiri Radiology       1729 N Ocean Ave   
8809                   Zwanger-Pesiri Radiology Group       759 Montauk Hwy.   
8810                   Zwanger-Pesiri Radiology Group                    LLP   

                  Address 2  Address 3             City State Zip Code  \
0                       NaN        NaN           Yakima    WA    98902   
1          31 Medical Group  Unit 6180  Air Post Office    AE     9604   
2                       NaN        NaN              APO    AP    96319   
3       374th Medical Group        NaN              APO    AP    96328   
4                       NaN        NaN        Scott AFB    IL    62225   
...                     ...        ...              ...   ...      ...   
8806                    NaN        NaN        Bay Shore    NY    11706   
8807                    NaN        NaN          Shirley    NY    11967   
8808                    NaN        NaN          Medford    NY    11763   
8809                    NaN        NaN       West Islip    NY    11795   
8810  150 East Sunrise Hwy.        NaN      Lindenhurst    NY    11757   

                Phone          Fax   Unnamed: 9 Unnamed: 10 Unnamed: 11  \
0         509574-3863  509249-5319          NaN         NaN         NaN   
1         3.90434E+11  3.90434E+11      3904343         NaN         NaN   
2         8.13118E+11      8117677          NaN         NaN         NaN   
3           425522510    425302026          NaN         NaN         NaN   
4         618256-1494  618256-7253          NaN         NaN         NaN   
...               ...          ...          ...         ...         ...   
8806      631444-5544  631666-9168          NaN         NaN         NaN   
8807      631444-5544  631870-8732          NaN         NaN         NaN   
8808      631444-5544  631870-8732          NaN         NaN         NaN   
8809  516798-42426001  631870-8732          NaN         NaN         NaN   
8810      631444-5544  631444-5544  631225-9550         NaN         NaN   

     Unnamed: 12  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  
...          ...  
8806         NaN  
8807         NaN  
8808         NaN  
8809         NaN  
8810         NaN  

[8811 rows x 13 columns]

In [ ]:
#keep only valuable rows
facility_filtered = raw_facility[['City','State', 'Zip Code']];
facility_filtered.head()

City State Zip Code
0           Yakima    WA    98902
1  Air Post Office    AE     9604
2              APO    AP    96319
3              APO    AP    96328
4        Scott AFB    IL    62225

In [ ]:
#count the number of values in each
facility_filtered['State'].value_counts().tail(50)

NJ            247
WI            215
MN            210
VA            205
TN            192
IN            179
AZ            171
PR            164
MO            159
MA            155
WA            149
IA            145
LA            145
KY            144
AL            141
CO            138
MD            132
OK            116
CT            114
SC            110
KS            109
OR            108
MS             99
NE             93
AR             83
NV             69
UT             64
WV             64
ID             49
ND             48
ME             48
SD             48
MT             47
NM             46
NH             44
HI             37
RI             34
AK             33
WY             30
DE             30
VT             15
DC             15
AE              6
AP              6
GU              5
VI              4
MP              1
36695           1
Washington      1
AS              1
Name: State, dtype: int64

In [ ]:
#random data exploration

#raw_facility[raw_facility['State'] == 'Washington']
# print(raw_facility.iloc[3773, 1])
# lol = raw_facility.iloc[3773, 1]
#print((raw_facility.iloc[2485,4]))
# print(raw_facility.iloc[8713,])
# raw_facility.iloc[8713,4] = raw_facility.iloc[8713,5]
# raw_facility.iloc[8713,5] = raw_facility.iloc[8713,6]
# raw_facility.iloc[8713,6] = raw_facility.iloc[8713,7]
# raw_facility.iloc[8713,7] = raw_facility.iloc[8713,8]
#print(raw_facility.iloc[3866,])

In [ ]:
#keep values whose 'State' value is a valid state
# relevant_facility_filtered = facility_filtered[~facility_filtered['State'].isin(['AL', 'AK', 'AZ', 'AR', 'AR', 'CA', 'CO', 'CT', 'DE', 'FL', 'GA',
#                                                                                 'HI', 'ID', 'IL', 'IN','IA', 'KS', 'KY', 'LA', 'ME', 'MD', 'MA', 'MI',
#                                                                                 'MN', 'MS', 'MO', 'MT', 'NE', 'NV', 'NH', 'NJ', 'NM', 'NY', 'NC', 'ND', 'OH',
#                                                                                 'OK', 'OR', 'PA', 'RI','SC', 'SD', 'TN', 'TX', 'UT', 'VT', 'VA', 'WA', 
#                                                                                 'WV', 'WI', 'WY', 'PR'])]['State'].value_counts().head(40);
# relevant_facility_filtered
relevant_facility_filtered = facility_filtered[facility_filtered['State'].isin(['AL', 'AK', 'AZ', 'AR', 'AR', 'CA', 'CO', 'CT', 'DE', 'FL', 'GA',
                                                                                'HI', 'ID', 'IL', 'IN','IA', 'KS', 'KY', 'LA', 'ME', 'MD', 'MA', 'MI',
                                                                                'MN', 'MS', 'MO', 'MT', 'NE', 'NV', 'NH', 'NJ', 'NM', 'NY', 'NC', 'ND', 'OH',
                                                                                'OK', 'OR', 'PA', 'RI','SC', 'SD', 'TN', 'TX', 'UT', 'VT', 'VA', 'WA', 
                                                                                'WV', 'WI', 'WY', 'DC'])];
relevant_facility_filtered

City State Zip Code
0           Yakima    WA    98902
4        Scott AFB    IL    62225
5            Butte    MT    59701
6     Morton Grove    IL    60053
8         Luke AFB    AZ    85309
...            ...   ...      ...
8806     Bay Shore    NY    11706
8807       Shirley    NY    11967
8808       Medford    NY    11763
8809    West Islip    NY    11795
8810   Lindenhurst    NY    11757

[8622 rows x 3 columns]

In [ ]:
zip_codes = relevant_facility_filtered.groupby("Zip Code").count().reset_index()[['Zip Code', 'City']];
zip_codes

Zip Code  City
0       01002     1
1       01086     1
2       01230     1
3       01432     1
4       01570     1
...       ...   ...
5849    99835     1
5850    99901     1
5851    99925     1
5852    99929     1
5853       NY     1

[5854 rows x 2 columns]

In [ ]:
#states = relevant_facility_filtered.groupby("State").count().reset_index()[['State', 'City']];
#states.to_csv('/content/drive/Shareddrives/facilities_per_state.csv')
#states

In [ ]:
#initialize the geolocator
geolocator = Nominatim(user_agent="geoapiExercises")

correct_based_on_zipcodes = relevant_facility_filtered[relevant_facility_filtered['Zip Code'].astype('str').str.len() == 5]

#print(correct_based_on_zipcodes['Zip Code'].tail())

correct_based_on_zipcodes.drop_duplicates(subset=['Zip Code'])

#create long and lat lists
latitudes = []
longitudes = []

#stored_locations = {}

for zip in correct_based_on_zipcodes['Zip Code']:
  # locationObj = None;

  locationObj = geolocator.geocode(zip)

  # if stored_locations.get(zip, None) == None:
  #   stored_locations[zip] = geolocator.geocode(zip)
  # else:
  #   locationObj = stored_locations[zip]
    
  if locationObj is not None:
    latitudes.append(locationObj.latitude)
    longitudes.append(locationObj.longitude)

# correct_based_on_zipcodes['Latitudes'] = latitudes
# correct_based_on_zipcodes['Longitudes'] = longitudes

us_map = folium.Map(location=[39.8283, -98.5795], zoom_start=4)

for i in range(len(latitudes)):
  folium.CircleMarker(
      location = [latitudes[i], longitudes[i]],
      radius = 1,
      color = 'green',
      fill = True,
      fill_color = 'green',
      fill_opacity=0.6
  ).add_to(us_map)

us_map